# Búsqueda Local

In [14]:
import numpy as np
import plotly.graph_objects as go
from math import cos, pi, sin

**INCISO B**: 	Implemente una   función en Python llamada evaluar_indice que  reciba como parámetro una tupla con la coordenada $(x,y)$ y retorne el valor del índice para dicha coordenada. 

In [15]:
def evaluar_indice(coords: tuple):
    X, Y = coords
    return (
        np.sin(X) * np.cos(Y) * np.exp(-(X**2 + Y**2)/50)   # ondulaciones atenuadas
        + 0.6*np.cos(2*X) * np.sin(2*Y) * np.exp(-(X**2 + Y**2)/80)  # picos secundarios
        + 2*np.cos(0.3*X) * np.cos(0.3*Y)                 # variación suave global
    )

**INCISO C:** Implemente una función en Python llamada generar_radar que reciba como parámetro una tupla con las coordenadas actuales $(x^t, y^t)$ y la longitud $\lambda$ y retorne las 8 coordenadas vecinas en una lista. 

In [16]:
def generar_radar(coor: tuple, lbd: float):
    x, y = coor
    coor1, coor2, coor3, coor4 = (x+lbd,y), (x-lbd,y), (x,y+lbd), (x,y-lbd)
    coor5, coor6, coor7, coor8 = (x+lbd,y+lbd), (x-lbd,y+lbd), (x+lbd,y-lbd), (x-lbd,y-lbd)
    return [coor1, coor2, coor3, coor4, coor5, coor6, coor7, coor8]

**INCISO D:** Implemente una función en Python llamada evaluar_factibilidad que reciba como parámetro una tupla con la coordenada $(x,y)$ y retorne True en caso de que se encuentre dentro de la región de estudio (cumpla todas las restricciones) y False de lo contrario.

In [17]:
def evaluar_factibilidad(coor: tuple):
    x_prim, y_prim = coor
    return x_prim >= -6 and y_prim <= 6 and x_prim <= 6 and y_prim >= -6 and x_prim + y_prim >= -6

**INCISO E:** Implemente una función en Python llamada encontrar_mejor_coor que reciba como parámetro un diccionario donde las llaves son coordenadas; 
y retorne la coordenada con menor índice y su índice. En esta función, 
debe evaluar si el diccionario que entra por parámetro está vacío, en cuyo 
caso deberá retornar False

In [18]:
#TODO
def encontrar_mejor_coor(my_dict: dict):
    if len(my_dict.keys()) != 0:
        max_coor = max(my_dict, key = my_dict.get)
        max_val = my_dict[max_coor]
        return (max_coor, max_val)
    else:
        return False

**NOTA:** A continuación se encuentra implementado el método de búsqueda local, el cual utilizará las funciones previamente implementadas para realizar el proceso de búsqueda local (corra esta celda antes de continuar con la implementación asegurandose de haber cumplido con los TODO previos).

In [19]:
#################################################
########### Método de búsqueda local ############
#################################################

# INCISO F. 
def busqueda_local(coord_ini: tuple, lbd: float):

    ### Incialización 
    ubicacion_actual = coord_ini
    objetivo_actual = evaluar_indice(ubicacion_actual)
    hay_mejora = True

    steps = [(ubicacion_actual, objetivo_actual)]  
    print(f"Iniciamos en: {coord_ini} con F.O. = {objetivo_actual}")

    ### Proceso iterativo
    while hay_mejora:
        
        mejor_objetivo = objetivo_actual

        # Generar las ubicaciones del radar
        radar = generar_radar(ubicacion_actual, lbd)
        my_dict = {}

        # Guardar las ubicaciones factibles con sus índices
        for coor in radar:
            if evaluar_factibilidad(coor):
                nuevo_objetivo = evaluar_indice(coor)
                my_dict[coor] = nuevo_objetivo

        # Buscar la mejor ubicación del radar y actualizar la posición
        res = encontrar_mejor_coor(my_dict)
        if res != False and res[1] > mejor_objetivo:
            ubicacion_actual = res[0]
            objetivo_actual = res[1]
            steps.append((ubicacion_actual, objetivo_actual))
            print(f"Mejora encontrada en: {ubicacion_actual} con F.O. = {objetivo_actual}")
         
        # Criterio de parda del proceso iterativo
        else:
            hay_mejora = False
    
    return steps

Determine las coordenadas iniciales $(x^0, y^0)$ y distancia del radar cuadrado de búsqueda (lbd)

In [20]:
#TODO
coor_inicial = np.array([4.5,0.5])
lbd = 0.05

Invoque el método de búsqueda local utilizando los argumentos definidos en la celda anterior.

In [21]:
#TODO
steps = busqueda_local(coor_inicial, lbd)

Iniciamos en: [4.5 0.5] con F.O. = -0.4922532704322492
Mejora encontrada en: (np.float64(4.45), np.float64(0.45)) con F.O. = -0.43664536917943436
Mejora encontrada en: (np.float64(4.4), np.float64(0.4)) con F.O. = -0.3739302757306404
Mejora encontrada en: (np.float64(4.3500000000000005), np.float64(0.35000000000000003)) con F.O. = -0.30574781871977397
Mejora encontrada en: (np.float64(4.300000000000001), np.float64(0.30000000000000004)) con F.O. = -0.2338827154913452
Mejora encontrada en: (np.float64(4.250000000000001), np.float64(0.25000000000000006)) con F.O. = -0.16019104553739505
Mejora encontrada en: (np.float64(4.200000000000001), np.float64(0.20000000000000007)) con F.O. = -0.08652400142991923
Mejora encontrada en: (np.float64(4.150000000000001), np.float64(0.15000000000000008)) con F.O. = -0.014652090279525298
Mejora encontrada en: (np.float64(4.100000000000001), np.float64(0.10000000000000007)) con F.O. = 0.05380703656646624
Mejora encontrada en: (np.float64(4.050000000000002)

Grafique el resultado de busqueda corriendo la celda que se muestra a continuación

In [22]:
# Malla
x_1, x_2 = np.linspace(-5, 5, 300), np.linspace(-5, 5, 300)
X, Y = np.meshgrid(x_1, x_2)
Z = evaluar_indice([X, Y])

# Extraer coordenadas
xs = [pt[0][0] for pt in steps]
ys = [pt[0][1] for pt in steps]
# Como el usuario ya da un "Z" (que puede no corresponder a la nueva función), lo uso directamente
zs = [float(pt[1]) for pt in steps]

# --- Superficie 3D interactiva con ruta ---
fig = go.Figure()

# Superficie base
fig.add_trace(go.Surface(x=X, y=Y, z=Z, colorscale='RdGy', reversescale=True, opacity=0.9))

# Ruta (línea roja con marcadores)
fig.add_trace(go.Scatter3d(
    x=xs, y=ys, z=zs,
    mode='lines+markers',
    line=dict(color='red', width=5),
    marker=dict(size=4, color='red'),
    name='Ruta (steps)'
))

fig.update_layout(
    title='Superficie 3D interactiva con ruta (steps)',
    scene=dict(
        xaxis_title='x-coordinate',
        yaxis_title='y-coordinate',
        zaxis_title='Valor'
    ),
    width=900, height=700
)


Aquí tienes un derivado **paso a paso**, listo para pegar en un Markdown de Google Colab (uso `$...$` y `$$...$$`):

---

## Función

Sea

$$
f(X,Y)=\underbrace{\sin X\,\cos Y\,e^{-\frac{X^2+Y^2}{50}}}_{T_1}
\;+\; \underbrace{0.6\,\cos(2X)\,\sin(2Y)\,e^{-\frac{X^2+Y^2}{80}}}_{T_2}
\;+\; \underbrace{2\,\cos(0.3X)\,\cos(0.3Y)}_{T_3}.
$$

Para abreviar, define

$$
E_1 = e^{-\frac{X^2+Y^2}{50}}, \qquad 
E_2 = e^{-\frac{X^2+Y^2}{80}}.
$$

Además,

$$
\frac{\partial}{\partial X}\!\left(-\frac{X^2+Y^2}{50}\right)=-\frac{2X}{50}=-\frac{X}{25}, 
\qquad
\frac{\partial}{\partial Y}\!\left(-\frac{X^2+Y^2}{50}\right)=-\frac{2Y}{50}=-\frac{Y}{25},
$$

$$
\frac{\partial}{\partial X}\!\left(-\frac{X^2+Y^2}{80}\right)=-\frac{2X}{80}=-\frac{X}{40}, 
\qquad
\frac{\partial}{\partial Y}\!\left(-\frac{X^2+Y^2}{80}\right)=-\frac{2Y}{80}=-\frac{Y}{40}.
$$

---

## Derivadas parciales de cada término

### 1) \$T\_1=\sin X,\cos Y,E\_1\$

**Reglas:** producto y cadena.

* Respecto de \$X\$:

$$
\frac{\partial T_1}{\partial X}
= (\cos X)\,\cos Y\,E_1
+ \sin X\,\cos Y\,\frac{\partial E_1}{\partial X}
= \cos X\,\cos Y\,E_1 - \frac{X}{25}\,\sin X\,\cos Y\,E_1.
$$

* Respecto de \$Y\$:

$$
\frac{\partial T_1}{\partial Y}
= \sin X\,(-\sin Y)\,E_1
+ \sin X\,\cos Y\,\frac{\partial E_1}{\partial Y}
= -\sin X\,\sin Y\,E_1 - \frac{Y}{25}\,\sin X\,\cos Y\,E_1.
$$

---

### 2) \$T\_2=0.6,\cos(2X),\sin(2Y),E\_2\$

**Reglas:** producto y cadena (\$\frac{d}{dX}\cos(2X)=-2\sin(2X)\$, \$\frac{d}{dY}\sin(2Y)=2\cos(2Y)\$).

* Respecto de \$X\$:

$$
\frac{\partial T_2}{\partial X}
=0.6\Big[\,(-2\sin(2X))\,\sin(2Y)\,E_2
+ \cos(2X)\,\sin(2Y)\,\frac{\partial E_2}{\partial X}\Big]
\\[2pt]
=0.6\Big[-2\,\sin(2X)\,\sin(2Y)\,E_2 \;-\; \frac{X}{40}\,\cos(2X)\,\sin(2Y)\,E_2\Big].
$$

* Respecto de \$Y\$:

$$
\frac{\partial T_2}{\partial Y}
=0.6\Big[\,\cos(2X)\,(2\cos(2Y))\,E_2
+ \cos(2X)\,\sin(2Y)\,\frac{\partial E_2}{\partial Y}\Big]
\\[2pt]
=0.6\Big[\,2\,\cos(2X)\,\cos(2Y)\,E_2 \;-\; \frac{Y}{40}\,\cos(2X)\,\sin(2Y)\,E_2\Big].
$$

---

### 3) \$T\_3=2,\cos(0.3X),\cos(0.3Y)\$

**Reglas:** derivada de coseno y producto (aunque aquí separable).

* Respecto de \$X\$:

$$
\frac{\partial T_3}{\partial X}
= 2\cdot(-0.3)\,\sin(0.3X)\,\cos(0.3Y)
= -0.6\,\sin(0.3X)\,\cos(0.3Y).
$$

* Respecto de \$Y\$:

$$
\frac{\partial T_3}{\partial Y}
= 2\cdot(-0.3)\,\cos(0.3X)\,\sin(0.3Y)
= -0.6\,\cos(0.3X)\,\sin(0.3Y).
$$

---

## Gradiente (sumando los tres términos)

$$
\boxed{
\frac{\partial f}{\partial X}
= \cos X\,\cos Y\,E_1 - \frac{X}{25}\,\sin X\,\cos Y\,E_1
+ 0.6\Big[-2\,\sin(2X)\,\sin(2Y)\,E_2 - \frac{X}{40}\,\cos(2X)\,\sin(2Y)\,E_2\Big]
- 0.6\,\sin(0.3X)\,\cos(0.3Y)
}
$$

$$
\boxed{
\frac{\partial f}{\partial Y}
= -\sin X\,\sin Y\,E_1 - \frac{Y}{25}\,\sin X\,\cos Y\,E_1
+ 0.6\Big[\,2\,\cos(2X)\,\cos(2Y)\,E_2 - \frac{Y}{40}\,\cos(2X)\,\sin(2Y)\,E_2\Big]
- 0.6\,\cos(0.3X)\,\sin(0.3Y)
}
$$

> (Recuerda: \$E\_1=e^{-\frac{X^2+Y^2}{50}}\$ y \$E\_2=e^{-\frac{X^2+Y^2}{80}}\$.)


In [23]:
def grad_evaluar_indice(coords: tuple):
    X, Y = coords
    
    E1 = np.exp(-(X**2 + Y**2)/50)
    E2 = np.exp(-(X**2 + Y**2)/80)
    
    # T1
    dT1_dX = (np.cos(X)*np.cos(Y)*E1
              - (2*X/50)*np.sin(X)*np.cos(Y)*E1)
    dT1_dY = (-np.sin(X)*np.sin(Y)*E1
              - (2*Y/50)*np.sin(X)*np.cos(Y)*E1)
    
    # T2
    dT2_dX = 0.6*((-2*np.sin(2*X)*np.sin(2*Y)*E2)
                  - (2*X/80)*np.cos(2*X)*np.sin(2*Y)*E2)
    dT2_dY = 0.6*((2*np.cos(2*X)*np.cos(2*Y)*E2)
                  - (2*Y/80)*np.cos(2*X)*np.sin(2*Y)*E2)
    
    # T3
    dT3_dX = -0.6*np.sin(0.3*X)*np.cos(0.3*Y)
    dT3_dY = -0.6*np.cos(0.3*X)*np.sin(0.3*Y)
    
    dfdX = dT1_dX + dT2_dX + dT3_dX
    dfdY = dT1_dY + dT2_dY + dT3_dY
    
    return np.array([dfdX, dfdY])

In [24]:
def gradient_descent(x0, f, grad, alpha=0.2, iters=50, eps=1e-06):
    """GD multidimensional con parada por norma del gradiente."""
    xs = [(x0.copy(), f(x0))]
    x = x0.copy()
    for _ in range(iters):
        g = grad(x)
        if np.linalg.norm(g) < eps: break
        x += alpha * g
        xs.append((x.copy(), f(x)))
    return xs

In [27]:
path_g2  = gradient_descent(coor_inicial, evaluar_indice, grad_evaluar_indice, alpha=0.08, iters=80)
steps = path_g2

In [28]:
# Malla
x_1, x_2 = np.linspace(-5, 5, 300), np.linspace(-5, 5, 300)
X, Y = np.meshgrid(x_1, x_2)
Z = evaluar_indice([X, Y])

# Extraer coordenadas
xs = [pt[0][0] for pt in steps]
ys = [pt[0][1] for pt in steps]
# Como el usuario ya da un "Z" (que puede no corresponder a la nueva función), lo uso directamente
zs = [float(pt[1]) for pt in steps]

# --- Superficie 3D interactiva con ruta ---
fig = go.Figure()

# Superficie base
fig.add_trace(go.Surface(x=X, y=Y, z=Z, colorscale='RdGy', reversescale=True, opacity=0.9))

# Ruta (línea roja con marcadores)
fig.add_trace(go.Scatter3d(
    x=xs, y=ys, z=zs,
    mode='lines+markers',
    line=dict(color='red', width=5),
    marker=dict(size=4, color='red'),
    name='Ruta (steps)'
))

fig.update_layout(
    title='Superficie 3D interactiva con ruta (steps)',
    scene=dict(
        xaxis_title='x-coordinate',
        yaxis_title='y-coordinate',
        zaxis_title='Valor'
    ),
    width=900, height=700
)
